# Resolution Enhancement: 1

In what is developing into a series of preprocessing notebooks, this particular article will address how to maximise peak detection in the Ringland signal. The problem is this - to fit the skewnorm distribution to a signal, the signal does need to possess somewhat normal peak shapes, and all peaks need to be detected. Currently, A number of peaks are not detected as they are not prominent enough. Furthermore, sharpening peaks into greater prominence will increase the depth of the gutters, the minima, such that it will make automated windowing simpler.

What are the available peak sharpening methods?

## Implementation of First Derivative Symmetrization

Before delving into advanced techniques, lets observe how the first derivative symmetrization affects the signal and peak detection


In [1]:
%reload_ext autoreload
%autoreload 2
from dataclasses import dataclass
from hplc_py.pipeline.preprocess_dashboard import DataSets, PreProcesser
from pandera.typing.polars import DataFrame, LazyFrame

import hvplot
import hvplot.pandas  # noqa
import pandera as pa
import panel as pn
import polars as pl
import sys

pl.Config.set_tbl_rows(10)
pn.extension()
pn.config.comms = "vscode"
sys.executable

dsets = DataSets()
ringland = dsets.ringland.fetch()
ringland.head()

shape: (5, 8)
┌─────┬───────────┬───────┬──────────┬───────────────────┬───────────────────┬──────────┬──────────┐
│ idx ┆ detection ┆ color ┆ varietal ┆ id                ┆ code_wine         ┆ time     ┆ signal   │
│ --- ┆ ---       ┆ ---   ┆ ---      ┆ ---               ┆ ---               ┆ ---      ┆ ---      │
│ i64 ┆ str       ┆ str   ┆ str      ┆ str               ┆ str               ┆ f64      ┆ f64      │
╞═════╪═══════════╪═══════╪══════════╪═══════════════════╪═══════════════════╪══════════╪══════════╡
│ 0   ┆ raw       ┆ red   ┆ shiraz   ┆ 7b085f32-4d69-4f7 ┆ a0301_2021 chris  ┆ 0.005833 ┆ 0.001952 │
│     ┆           ┆       ┆          ┆ 8-b49b-4d32871d…  ┆ ringland shiraz   ┆          ┆          │
│ 1   ┆ raw       ┆ red   ┆ shiraz   ┆ 7b085f32-4d69-4f7 ┆ a0301_2021 chris  ┆ 0.0125   ┆ 0.001825 │
│     ┆           ┆       ┆          ┆ 8-b49b-4d32871d…  ┆ ringland shiraz   ┆          ┆          │
│ 2   ┆ raw       ┆ red   ┆ shiraz   ┆ 7b085f32-4d69-4f7 ┆ a0301_2021 chris  ┆ 0.019167 ┆ 0.002004 │
│     ┆           ┆       ┆          ┆ 8-b49b-4d32871d…  ┆ ringland shiraz   ┆          ┆          │
│ 3   ┆ raw       ┆ red   ┆ shiraz   ┆ 7b085f32-4d69-4f7 ┆ a0301_2021 chris  ┆ 0.025833 ┆ 0.002861 │
│     ┆           ┆       ┆          ┆ 8-b49b-4d32871d…  ┆ ringland shiraz   ┆          ┆          │
│ 4   ┆ raw       ┆ red   ┆ shiraz   ┆ 7b085f32-4d69-4f7 ┆ a0301_2021 chris  ┆ 0.0325   ┆ 0.003964 │
│     ┆           ┆       ┆          ┆ 8-b49b-4d32871d…  ┆ ringland shiraz   ┆          ┆          │
└─────┴───────────┴───────┴──────────┴───────────────────┴───────────────────┴──────────┴──────────┘

In [2]:
raw_data = ringland[["time", "signal"]]
raw_data

shape: (4_050, 2)
┌───────────┬──────────┐
│ time      ┆ signal   │
│ ---       ┆ ---      │
│ f64       ┆ f64      │
╞═══════════╪══════════╡
│ 0.005833  ┆ 0.001952 │
│ 0.0125    ┆ 0.001825 │
│ 0.019167  ┆ 0.002004 │
│ 0.025833  ┆ 0.002861 │
│ 0.0325    ┆ 0.003964 │
│ …         ┆ …        │
│ 26.9725   ┆ 1.733087 │
│ 26.979167 ┆ 1.732111 │
│ 26.985833 ┆ 1.731098 │
│ 26.9925   ┆ 1.730151 │
│ 26.999167 ┆ 1.728989 │
└───────────┴──────────┘

## Enhancement by Subtraction of Derivatives (Apprimxated as finite difference)

In a DataFrame, this can be calculated by shifting Y forward one and back one then performing the calculation across the rows:

$$f_i'=\frac{f_{i+1}-f_{i-1}}{2 \Delta x_i}$$

and the second derivative is:

$$f^"_i=\frac{
  f_{i-1}-2f_i+f_{i+1}
  }
  {
    \Delta x^2
  }$$

  Where: $\Delta x = x_{i+1}-x_{i-1}$

  This assumes that x is evenly spaced

First create an evenly spaced x (time) based on the mean step

In [3]:
raw_data.select(pl.col("time").diff().forward_fill().backward_fill()).describe()

shape: (9, 2)
┌────────────┬────────────┐
│ statistic  ┆ time       │
│ ---        ┆ ---        │
│ str        ┆ f64        │
╞════════════╪════════════╡
│ count      ┆ 4050.0     │
│ null_count ┆ 0.0        │
│ mean       ┆ 0.006667   │
│ std        ┆ 1.1460e-15 │
│ min        ┆ 0.006667   │
│ 25%        ┆ 0.006667   │
│ 50%        ┆ 0.006667   │
│ 75%        ┆ 0.006667   │
│ max        ┆ 0.006667   │
└────────────┴────────────┘

Actually, looks like this already is resampled. TODO: integrate resampling into main preprocessing

Next, shift the columns forward or back such that for each row "i", it also contains "i-1", and "i+1".

In [4]:
# add a row index to track movement forward and back. Shifting by 1 moves the array back one according to the current i, i.e. "idx_1f" is i = -1 relative to i = 0.
shifted_data = (
    raw_data
    .with_row_index("idx")
    .with_columns(
        pl.col('idx').shift(1).alias("idx_i-1"),
        pl.col('time').shift(1).alias("time_i-1"),
        pl.col('signal').shift(1).alias("signal_i-1"),
        pl.col('idx').shift(-1).alias("idx_i+1"),
        pl.col('time').shift(-1).alias("time_i+1"),
        pl.col('signal').shift(-1).alias("signal_i+1")
    )
    )  # fmt: skip

shifted_data

shape: (4_050, 9)
┌──────┬───────────┬──────────┬─────────┬───────────┬────────────┬─────────┬───────────┬───────────┐
│ idx  ┆ time      ┆ signal   ┆ idx_i-1 ┆ time_i-1  ┆ signal_i-1 ┆ idx_i+1 ┆ time_i+1  ┆ signal_i+ │
│ ---  ┆ ---       ┆ ---      ┆ ---     ┆ ---       ┆ ---        ┆ ---     ┆ ---       ┆ 1         │
│ u32  ┆ f64       ┆ f64      ┆ u32     ┆ f64       ┆ f64        ┆ u32     ┆ f64       ┆ ---       │
│      ┆           ┆          ┆         ┆           ┆            ┆         ┆           ┆ f64       │
╞══════╪═══════════╪══════════╪═════════╪═══════════╪════════════╪═════════╪═══════════╪═══════════╡
│ 0    ┆ 0.005833  ┆ 0.001952 ┆ null    ┆ null      ┆ null       ┆ 1       ┆ 0.0125    ┆ 0.001825  │
│ 1    ┆ 0.0125    ┆ 0.001825 ┆ 0       ┆ 0.005833  ┆ 0.001952   ┆ 2       ┆ 0.019167  ┆ 0.002004  │
│ 2    ┆ 0.019167  ┆ 0.002004 ┆ 1       ┆ 0.0125    ┆ 0.001825   ┆ 3       ┆ 0.025833  ┆ 0.002861  │
│ 3    ┆ 0.025833  ┆ 0.002861 ┆ 2       ┆ 0.019167  ┆ 0.002004   ┆ 4       ┆ 0.0325    ┆ 0.003964  │
│ 4    ┆ 0.0325    ┆ 0.003964 ┆ 3       ┆ 0.025833  ┆ 0.002861   ┆ 5       ┆ 0.039167  ┆ 0.005022  │
│ …    ┆ …         ┆ …        ┆ …       ┆ …         ┆ …          ┆ …       ┆ …         ┆ …         │
│ 4045 ┆ 26.9725   ┆ 1.733087 ┆ 4044    ┆ 26.965833 ┆ 1.733929   ┆ 4046    ┆ 26.979167 ┆ 1.732111  │
│ 4046 ┆ 26.979167 ┆ 1.732111 ┆ 4045    ┆ 26.9725   ┆ 1.733087   ┆ 4047    ┆ 26.985833 ┆ 1.731098  │
│ 4047 ┆ 26.985833 ┆ 1.731098 ┆ 4046    ┆ 26.979167 ┆ 1.732111   ┆ 4048    ┆ 26.9925   ┆ 1.730151  │
│ 4048 ┆ 26.9925   ┆ 1.730151 ┆ 4047    ┆ 26.985833 ┆ 1.731098   ┆ 4049    ┆ 26.999167 ┆ 1.728989  │
│ 4049 ┆ 26.999167 ┆ 1.728989 ┆ 4048    ┆ 26.9925   ┆ 1.730151   ┆ null    ┆ null      ┆ null      │
└──────┴───────────┴──────────┴─────────┴───────────┴────────────┴─────────┴───────────┴───────────┘

Then define the expressions

In [5]:
# first derivative

first_central_diff = (
    (pl.col("signal_i+1").sub(pl.col("signal_i-1")))
     .truediv(
         (pl.col("time_i+1").sub(pl.col("time_i-1"))).mul(pl.lit(2))
         )
     )  # fmt: skip

# second derivative

second_central_diff = (
    (pl.col("signal_i-1") - pl.lit(2).mul("signal") + pl.col("signal_i+1")
     )
    .truediv((pl.col("time_i+1").sub(pl.col("time_i-1"))).pow(2))
)  # fmt: skip

And apply

In [6]:
preprocessed_data_df = (
    shifted_data
    .select(
        pl.col('time'),
        pl.col('signal'),
        first_central_diff.alias('first_central_diff'),
        second_central_diff.alias('second_central_diff')
    )
)  # fmt: skip
preprocessed_data_df

shape: (4_050, 4)
┌───────────┬──────────┬────────────────────┬─────────────────────┐
│ time      ┆ signal   ┆ first_central_diff ┆ second_central_diff │
│ ---       ┆ ---      ┆ ---                ┆ ---                 │
│ f64       ┆ f64      ┆ f64                ┆ f64                 │
╞═══════════╪══════════╪════════════════════╪═════════════════════╡
│ 0.005833  ┆ 0.001952 ┆ null               ┆ null                │
│ 0.0125    ┆ 0.001825 ┆ 0.001956           ┆ 1.71829             │
│ 0.019167  ┆ 0.002004 ┆ 0.038836           ┆ 3.813766            │
│ 0.025833  ┆ 0.002861 ┆ 0.073481           ┆ 1.383014            │
│ 0.0325    ┆ 0.003964 ┆ 0.081025           ┆ -0.251457           │
│ …         ┆ …        ┆ …                  ┆ …                   │
│ 26.9725   ┆ 1.733087 ┆ -0.068173          ┆ -0.754371           │
│ 26.979167 ┆ 1.732111 ┆ -0.074599          ┆ -0.209548           │
│ 26.985833 ┆ 1.731098 ┆ -0.073481          ┆ 0.377186            │
│ 26.9925   ┆ 1.730151 ┆ -0.079069          ┆ -1.215376           │
│ 26.999167 ┆ 1.728989 ┆ null               ┆ null                │
└───────────┴──────────┴────────────────────┴─────────────────────┘

and plot the results

In [7]:
preprocessed_data_df.plot(x="time", y="signal")

:Curve   [time]   (signal)

In [8]:
preprocessed_data_df.plot(
    x="time",
    y=["signal", "first_central_diff", "second_central_diff"],
    subplots=True,
    shared_axes=False,
)

:NdLayout   [Variable]
   :Curve   [time]   (value)

Now as we can see, the first and second derivatives are on much larger scales than the initial signal, which is to be expected considering the sharpness and prominence of the signal maxima. Thus the weighting factor mentioned above. Now define a symmetric difference expression, and as usual, the parameter space needs to be explored

In [9]:
# application of first diff
k1 = 0.02
preprocessed_data_df = (
    preprocessed_data_df
    .with_columns(
        pl.col("first_central_diff").mul(k1).alias("weighted_first_diff")
    )
    .with_columns(
        pl.col("signal").sub(pl.col("weighted_first_diff")).alias("signal_adjusted_first_diff")
    )
)  # fmt: skip

(
    preprocessed_data_df 
        .plot(
            x="time",
            y=["signal", "weighted_first_diff", "signal_adjusted_first_diff"],
            alpha=[0.5, 0.2, 1],
        )
        .opts(height=750, width=1000)
)  # fmt: skip

:NdOverlay   [Variable]
   :Curve   [time]   (value)

a weighting of 0.02 begins to resolve some peaks but does not do nearly enough

And the second diff?

In [10]:
# application of first diff
k2 = 6e-4
preprocessed_data_df = (
    preprocessed_data_df.with_columns(
        pl.col("second_central_diff").mul(k2).alias("weighted_second_diff")
    )
    .with_columns(
        pl.col("signal").sub(pl.col("weighted_second_diff")).alias("signal_adjusted_2nd_diff")
    )
)  # fmt: skip

(
    preprocessed_data_df 
        .plot(
            x="time",
            y=["signal", "weighted_second_diff", "signal_adjusted_2nd_diff"],
            alpha=[0.5, 0.2, 1],
        )
        .opts(height=750, width=1000)
)  # fmt: skip

:NdOverlay   [Variable]
   :Curve   [time]   (value)

a weighting of 6e-4 begins to resolve shoulder peaks without dipping below the baseline. The highly convoluted region between 4 and 5 mins is not nearly resolved enough though.

and what if both are subtracted at the same time?

In [11]:
preprocessed_data_df

shape: (4_050, 8)
┌───────────┬──────────┬────────────┬────────────┬────────────┬────────────┬───────────┬───────────┐
│ time      ┆ signal   ┆ first_cent ┆ second_cen ┆ weighted_f ┆ signal_adj ┆ weighted_ ┆ signal_ad │
│ ---       ┆ ---      ┆ ral_diff   ┆ tral_diff  ┆ irst_diff  ┆ usted_firs ┆ second_di ┆ justed_2n │
│ f64       ┆ f64      ┆ ---        ┆ ---        ┆ ---        ┆ t_diff     ┆ ff        ┆ d_diff    │
│           ┆          ┆ f64        ┆ f64        ┆ f64        ┆ ---        ┆ ---       ┆ ---       │
│           ┆          ┆            ┆            ┆            ┆ f64        ┆ f64       ┆ f64       │
╞═══════════╪══════════╪════════════╪════════════╪════════════╪════════════╪═══════════╪═══════════╡
│ 0.005833  ┆ 0.001952 ┆ null       ┆ null       ┆ null       ┆ null       ┆ null      ┆ null      │
│ 0.0125    ┆ 0.001825 ┆ 0.001956   ┆ 1.71829    ┆ 0.000039   ┆ 0.001786   ┆ 0.001031  ┆ 0.000794  │
│ 0.019167  ┆ 0.002004 ┆ 0.038836   ┆ 3.813766   ┆ 0.000777   ┆ 0.001227   ┆ 0.002288  ┆ -0.000284 │
│ 0.025833  ┆ 0.002861 ┆ 0.073481   ┆ 1.383014   ┆ 0.00147    ┆ 0.001391   ┆ 0.00083   ┆ 0.002031  │
│ 0.0325    ┆ 0.003964 ┆ 0.081025   ┆ -0.251457  ┆ 0.001621   ┆ 0.002343   ┆ -0.000151 ┆ 0.004115  │
│ …         ┆ …        ┆ …          ┆ …          ┆ …          ┆ …          ┆ …         ┆ …         │
│ 26.9725   ┆ 1.733087 ┆ -0.068173  ┆ -0.754371  ┆ -0.001363  ┆ 1.73445    ┆ -0.000453 ┆ 1.73354   │
│ 26.979167 ┆ 1.732111 ┆ -0.074599  ┆ -0.209548  ┆ -0.001492  ┆ 1.733603   ┆ -0.000126 ┆ 1.732237  │
│ 26.985833 ┆ 1.731098 ┆ -0.073481  ┆ 0.377186   ┆ -0.00147   ┆ 1.732567   ┆ 0.000226  ┆ 1.730871  │
│ 26.9925   ┆ 1.730151 ┆ -0.079069  ┆ -1.215376  ┆ -0.001581  ┆ 1.731733   ┆ -0.000729 ┆ 1.730881  │
│ 26.999167 ┆ 1.728989 ┆ null       ┆ null       ┆ null       ┆ null       ┆ null      ┆ null      │
└───────────┴──────────┴────────────┴────────────┴────────────┴────────────┴───────────┴───────────┘

In [12]:
def calculate_derivative_subtractions(
    df: pl.DataFrame, k1: float = 2e-2, k2: float = 6e-4
):
    # add a row index to track movement forward and back. Shifting by 1 moves the array back one according to the current i, i.e. "idx_1f" is i = -1 relative to i = 0.
    shifted_data = (
    df
    .with_row_index("idx")
    .with_columns(
        pl.col('idx').shift(1).alias("idx_i-1"),
        pl.col('time').shift(1).alias("time_i-1"),
        pl.col('signal').shift(1).alias("signal_i-1"),
        pl.col('idx').shift(-1).alias("idx_i+1"),
        pl.col('time').shift(-1).alias("time_i+1"),
        pl.col('signal').shift(-1).alias("signal_i+1")
    )
    )  # fmt: skip

    diffs = (
    shifted_data.select(
        pl.col('signal'),
        first_central_diff.alias('first_central_diff'),
        second_central_diff.alias('second_central_diff')
    )
    .with_columns(
        pl.col("first_central_diff").mul(k1).alias("weighted_first_diff")
    )
    .with_columns(
        pl.col("signal").sub(pl.col("weighted_first_diff")).alias("signal_adjusted_first_diff")
    )
    .with_columns(
        pl.col("second_central_diff").mul(k2).alias("weighted_second_diff")
    )
    .with_columns(
        pl.col("signal").sub(pl.col("weighted_second_diff")).alias("signal_adjusted_2nd_diff")
    )
    .with_columns(
    pl.col("signal")
    .sub(pl.col("weighted_first_diff"))
    .sub(pl.col("weighted_second_diff"))
    .alias("double_subtraction")
    )
    )  # fmt: skip

    out = pl.concat([df, diffs.drop("signal")], how="horizontal")
    display(out)
    return out


subtracted_data_without_baseline_correction = raw_data.pipe(
    calculate_derivative_subtractions
)

display(subtracted_data_without_baseline_correction)
(
    subtracted_data_without_baseline_correction.plot(
        x="time",
        y=["signal", "signal_adjusted_2nd_diff", "double_subtraction"],
        alpha=[0.5, 0.5],
    )
).opts(height=750, width=1000)

shape: (4_050, 9)
┌──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┐
│ time     ┆ signal   ┆ first_ce ┆ second_c ┆ weighted ┆ signal_a ┆ weighted ┆ signal_a ┆ double_s │
│ ---      ┆ ---      ┆ ntral_di ┆ entral_d ┆ _first_d ┆ djusted_ ┆ _second_ ┆ djusted_ ┆ ubtracti │
│ f64      ┆ f64      ┆ ff       ┆ iff      ┆ iff      ┆ first_di ┆ diff     ┆ 2nd_diff ┆ on       │
│          ┆          ┆ ---      ┆ ---      ┆ ---      ┆ ff       ┆ ---      ┆ ---      ┆ ---      │
│          ┆          ┆ f64      ┆ f64      ┆ f64      ┆ ---      ┆ f64      ┆ f64      ┆ f64      │
│          ┆          ┆          ┆          ┆          ┆ f64      ┆          ┆          ┆          │
╞══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╡
│ 0.005833 ┆ 0.001952 ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│ 0.0125   ┆ 0.001825 ┆ 0.001956 ┆ 1.71829  ┆ 0.000039 ┆ 0.001786 ┆ 0.001031 ┆ 0.000794 ┆ 0.000755 │
│ 0.019167 ┆ 0.002004 ┆ 0.038836 ┆ 3.813766 ┆ 0.000777 ┆ 0.001227 ┆ 0.002288 ┆ -0.00028 ┆ -0.00106 │
│          ┆          ┆          ┆          ┆          ┆          ┆          ┆ 4        ┆ 1        │
│ 0.025833 ┆ 0.002861 ┆ 0.073481 ┆ 1.383014 ┆ 0.00147  ┆ 0.001391 ┆ 0.00083  ┆ 0.002031 ┆ 0.000562 │
│ 0.0325   ┆ 0.003964 ┆ 0.081025 ┆ -0.25145 ┆ 0.001621 ┆ 0.002343 ┆ -0.00015 ┆ 0.004115 ┆ 0.002494 │
│          ┆          ┆          ┆ 7        ┆          ┆          ┆ 1        ┆          ┆          │
│ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        │
│ 26.9725  ┆ 1.733087 ┆ -0.06817 ┆ -0.75437 ┆ -0.00136 ┆ 1.73445  ┆ -0.00045 ┆ 1.73354  ┆ 1.734903 │
│          ┆          ┆ 3        ┆ 1        ┆ 3        ┆          ┆ 3        ┆          ┆          │
│ 26.97916 ┆ 1.732111 ┆ -0.07459 ┆ -0.20954 ┆ -0.00149 ┆ 1.733603 ┆ -0.00012 ┆ 1.732237 ┆ 1.733729 │
│ 7        ┆          ┆ 9        ┆ 8        ┆ 2        ┆          ┆ 6        ┆          ┆          │
│ 26.98583 ┆ 1.731098 ┆ -0.07348 ┆ 0.377186 ┆ -0.00147 ┆ 1.732567 ┆ 0.000226 ┆ 1.730871 ┆ 1.732341 │
│ 3        ┆          ┆ 1        ┆          ┆          ┆          ┆          ┆          ┆          │
│ 26.9925  ┆ 1.730151 ┆ -0.07906 ┆ -1.21537 ┆ -0.00158 ┆ 1.731733 ┆ -0.00072 ┆ 1.730881 ┆ 1.732462 │
│          ┆          ┆ 9        ┆ 6        ┆ 1        ┆          ┆ 9        ┆          ┆          │
│ 26.99916 ┆ 1.728989 ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│ 7        ┆          ┆          ┆          ┆          ┆          ┆          ┆          ┆          │
└──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┘

shape: (4_050, 9)
┌──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┐
│ time     ┆ signal   ┆ first_ce ┆ second_c ┆ weighted ┆ signal_a ┆ weighted ┆ signal_a ┆ double_s │
│ ---      ┆ ---      ┆ ntral_di ┆ entral_d ┆ _first_d ┆ djusted_ ┆ _second_ ┆ djusted_ ┆ ubtracti │
│ f64      ┆ f64      ┆ ff       ┆ iff      ┆ iff      ┆ first_di ┆ diff     ┆ 2nd_diff ┆ on       │
│          ┆          ┆ ---      ┆ ---      ┆ ---      ┆ ff       ┆ ---      ┆ ---      ┆ ---      │
│          ┆          ┆ f64      ┆ f64      ┆ f64      ┆ ---      ┆ f64      ┆ f64      ┆ f64      │
│          ┆          ┆          ┆          ┆          ┆ f64      ┆          ┆          ┆          │
╞══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╡
│ 0.005833 ┆ 0.001952 ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│ 0.0125   ┆ 0.001825 ┆ 0.001956 ┆ 1.71829  ┆ 0.000039 ┆ 0.001786 ┆ 0.001031 ┆ 0.000794 ┆ 0.000755 │
│ 0.019167 ┆ 0.002004 ┆ 0.038836 ┆ 3.813766 ┆ 0.000777 ┆ 0.001227 ┆ 0.002288 ┆ -0.00028 ┆ -0.00106 │
│          ┆          ┆          ┆          ┆          ┆          ┆          ┆ 4        ┆ 1        │
│ 0.025833 ┆ 0.002861 ┆ 0.073481 ┆ 1.383014 ┆ 0.00147  ┆ 0.001391 ┆ 0.00083  ┆ 0.002031 ┆ 0.000562 │
│ 0.0325   ┆ 0.003964 ┆ 0.081025 ┆ -0.25145 ┆ 0.001621 ┆ 0.002343 ┆ -0.00015 ┆ 0.004115 ┆ 0.002494 │
│          ┆          ┆          ┆ 7        ┆          ┆          ┆ 1        ┆          ┆          │
│ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        │
│ 26.9725  ┆ 1.733087 ┆ -0.06817 ┆ -0.75437 ┆ -0.00136 ┆ 1.73445  ┆ -0.00045 ┆ 1.73354  ┆ 1.734903 │
│          ┆          ┆ 3        ┆ 1        ┆ 3        ┆          ┆ 3        ┆          ┆          │
│ 26.97916 ┆ 1.732111 ┆ -0.07459 ┆ -0.20954 ┆ -0.00149 ┆ 1.733603 ┆ -0.00012 ┆ 1.732237 ┆ 1.733729 │
│ 7        ┆          ┆ 9        ┆ 8        ┆ 2        ┆          ┆ 6        ┆          ┆          │
│ 26.98583 ┆ 1.731098 ┆ -0.07348 ┆ 0.377186 ┆ -0.00147 ┆ 1.732567 ┆ 0.000226 ┆ 1.730871 ┆ 1.732341 │
│ 3        ┆          ┆ 1        ┆          ┆          ┆          ┆          ┆          ┆          │
│ 26.9925  ┆ 1.730151 ┆ -0.07906 ┆ -1.21537 ┆ -0.00158 ┆ 1.731733 ┆ -0.00072 ┆ 1.730881 ┆ 1.732462 │
│          ┆          ┆ 9        ┆ 6        ┆ 1        ┆          ┆ 9        ┆          ┆          │
│ 26.99916 ┆ 1.728989 ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│ 7        ┆          ┆          ┆          ┆          ┆          ┆          ┆          ┆          │
└──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┘

:NdOverlay   [Variable]
   :Curve   [time]   (value)

Looks good, appears to moderate the more extreme effects of the second derivative subtraction. A lot of peaks are still not resolved enough though.

Weightings pairs and observations:

1. k1=k1 = 2e-2, k2 = 6e-4. highest I can go without going below the baseline. Good, but plenty of shoulder peaks remain, especially in regions 4 - 5, 5 - 6, 6 - 7, 6 - 9, 11 - 12, 12 - 12.5, etc.

What happens if we subtract the baseline first? It shouldnt make a difference, although it would mean that the weighting would be different - the base value of the derivative wouldnt change, but its magnitude in relation to the signal would.

### Resolution Enhancement After Baseline Correction

Do the same as above but correct the baseline first.


In [13]:
prepro = PreProcesser()
prepro.ingest_signal(ringland, time_col="time", amp_col="signal")
prepro.signal_adjustment(bcorr__n_iter=39)
prepro.signal

adjusted_signal = prepro.signal.select(["time", "adjusted_signal"])
adjusted_signal

Performing baseline correction: 100%|██████████| 39/39 [00:00<00:00, 592.22it/s]


shape: (4_050, 2)
┌───────────┬─────────────────┐
│ time      ┆ adjusted_signal │
│ ---       ┆ ---             │
│ f64       ┆ f64             │
╞═══════════╪═════════════════╡
│ 0.005833  ┆ 2.2204e-16      │
│ 0.0125    ┆ -6.6613e-16     │
│ 0.019167  ┆ -4.4409e-16     │
│ 0.025833  ┆ -4.4409e-16     │
│ 0.0325    ┆ 0.000023        │
│ …         ┆ …               │
│ 26.9725   ┆ 0.000444        │
│ 26.979167 ┆ 0.000296        │
│ 26.985833 ┆ 0.000094        │
│ 26.9925   ┆ 0.000108        │
│ 26.999167 ┆ -4.4409e-16     │
└───────────┴─────────────────┘

In [14]:
subtracted_data_after_baseline_sub = calculate_derivative_subtractions(
    adjusted_signal.rename({"adjusted_signal": "signal"})
)

(
    subtracted_data_after_baseline_sub.plot(
        x="time",
        y=["signal", "signal_adjusted_2nd_diff", "double_subtraction"],
        alpha=[0.5, 0.5],
    )
).opts(height=750, width=1000)

shape: (4_050, 9)
┌──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┬──────────┐
│ time     ┆ signal   ┆ first_ce ┆ second_c ┆ weighted ┆ signal_a ┆ weighted ┆ signal_a ┆ double_s │
│ ---      ┆ ---      ┆ ntral_di ┆ entral_d ┆ _first_d ┆ djusted_ ┆ _second_ ┆ djusted_ ┆ ubtracti │
│ f64      ┆ f64      ┆ ff       ┆ iff      ┆ iff      ┆ first_di ┆ diff     ┆ 2nd_diff ┆ on       │
│          ┆          ┆ ---      ┆ ---      ┆ ---      ┆ ff       ┆ ---      ┆ ---      ┆ ---      │
│          ┆          ┆ f64      ┆ f64      ┆ f64      ┆ ---      ┆ f64      ┆ f64      ┆ f64      │
│          ┆          ┆          ┆          ┆          ┆ f64      ┆          ┆          ┆          │
╞══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╪══════════╡
│ 0.005833 ┆ 2.2204e- ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│          ┆ 16       ┆          ┆          ┆          ┆          ┆          ┆          ┆          │
│ 0.0125   ┆ -6.6613e ┆ -2.4980e ┆ 6.2450e- ┆ -4.9960e ┆ -1.6653e ┆ 3.7470e- ┆ -4.4131e ┆ -3.9135e │
│          ┆ -16      ┆ -14      ┆ 12       ┆ -16      ┆ -16      ┆ 15       ┆ -15      ┆ -15      │
│ 0.019167 ┆ -4.4409e ┆ 8.3267e- ┆ -1.2490e ┆ 1.6653e- ┆ -6.1062e ┆ -7.4940e ┆ 3.0531e- ┆ 1.3878e- │
│          ┆ -16      ┆ 15       ┆ -12      ┆ 16       ┆ -16      ┆ -16      ┆ 16       ┆ 16       │
│ 0.025833 ┆ -4.4409e ┆ 0.000858 ┆ 0.12866  ┆ 0.000017 ┆ -0.00001 ┆ 0.000077 ┆ -0.00007 ┆ -0.00009 │
│          ┆ -16      ┆          ┆          ┆          ┆ 7        ┆          ┆ 7        ┆ 4        │
│ 0.0325   ┆ 0.000023 ┆ 0.050325 ┆ 7.291505 ┆ 0.001007 ┆ -0.00098 ┆ 0.004375 ┆ -0.00435 ┆ -0.00535 │
│          ┆          ┆          ┆          ┆          ┆ 4        ┆          ┆ 2        ┆ 9        │
│ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        ┆ …        │
│ 26.9725  ┆ 0.000444 ┆ -0.00539 ┆ -0.86027 ┆ -0.00010 ┆ 0.000552 ┆ -0.00051 ┆ 0.00096  ┆ 0.001068 │
│          ┆          ┆          ┆          ┆ 8        ┆          ┆ 6        ┆          ┆          │
│ 26.97916 ┆ 0.000296 ┆ -0.01313 ┆ -0.30066 ┆ -0.00026 ┆ 0.000558 ┆ -0.00018 ┆ 0.000476 ┆ 0.000739 │
│ 7        ┆          ┆          ┆ 9        ┆ 3        ┆          ┆          ┆          ┆          │
│ 26.98583 ┆ 0.000094 ┆ -0.00703 ┆ 1.215531 ┆ -0.00014 ┆ 0.000235 ┆ 0.000729 ┆ -0.00063 ┆ -0.00049 │
│ 3        ┆          ┆ 1        ┆          ┆ 1        ┆          ┆          ┆ 5        ┆ 5        │
│ 26.9925  ┆ 0.000108 ┆ -0.00352 ┆ -0.68926 ┆ -0.00007 ┆ 0.000179 ┆ -0.00041 ┆ 0.000522 ┆ 0.000592 │
│          ┆          ┆ 2        ┆ 2        ┆          ┆          ┆ 4        ┆          ┆          │
│ 26.99916 ┆ -4.4409e ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     ┆ null     │
│ 7        ┆ -16      ┆          ┆          ┆          ┆          ┆          ┆          ┆          │
└──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┴──────────┘

:NdOverlay   [Variable]
   :Curve   [time]   (value)

First thing to notice is that it is a lot noisier. A direct comparison is needed:

In [15]:
inter_1 = subtracted_data_without_baseline_correction.select(
    pl.col("time"), pl.col("double_subtraction").alias("no_baseline_sub")
)
inter_2 = subtracted_data_after_baseline_sub.select(
    pl.col("double_subtraction").alias("with_baseline_sub")
)

compare = pl.concat([inter_1, inter_2], how="horizontal")
compare.plot(
    x="time",
    y=["no_baseline_sub", "with_baseline_sub"],
    alpha=[0.75, 0.75],
    height=500,
    width=1000,
)

:NdOverlay   [Variable]
   :Curve   [time]   (value)

Looks like it needs smoothing before derivative calculations. Use Savitsky-Golay. Scipy has one, use that.

In [16]:
def deriv_subtraction_with_baseline_correction_and_smoothing(input_data):
    prepro = PreProcesser()
    prepro.ingest_signal(input_data, time_col="time", amp_col="signal")
    prepro.signal_adjustment(bcorr__n_iter=39)
    prepro.signal

    from scipy import signal

    adjusted_signal = prepro.signal.select(["time", "adjusted_signal", "background"])

    savgol_input = adjusted_signal.to_series(
        adjusted_signal.columns.index("adjusted_signal")
    ).to_numpy()

    smoothed = signal.savgol_filter(savgol_input, window_length=20, polyorder=2)

    adjusted_signal = adjusted_signal.with_columns(
        pl.Series(name="smoothed", values=smoothed)
    )

    display(adjusted_signal)
    display(
        adjusted_signal.plot(
            x="time",
            y=["adjusted_signal", "smoothed"],
            alpha=[0.75, 0.75],
            width=1000,
            height=500,
            xlim=(20, 26),
            grid=True,
        )
    )

    return adjusted_signal


smoothed_signal = ringland.pipe(
    deriv_subtraction_with_baseline_correction_and_smoothing
)

Performing baseline correction: 100%|██████████| 39/39 [00:00<00:00, 536.48it/s]


shape: (4_050, 4)
┌───────────┬─────────────────┬────────────┬───────────┐
│ time      ┆ adjusted_signal ┆ background ┆ smoothed  │
│ ---       ┆ ---             ┆ ---        ┆ ---       │
│ f64       ┆ f64             ┆ f64        ┆ f64       │
╞═══════════╪═════════════════╪════════════╪═══════════╡
│ 0.005833  ┆ 2.2204e-16      ┆ 0.001952   ┆ -0.005903 │
│ 0.0125    ┆ -6.6613e-16     ┆ 0.001825   ┆ -0.002536 │
│ 0.019167  ┆ -4.4409e-16     ┆ 0.002004   ┆ 0.000442  │
│ 0.025833  ┆ -4.4409e-16     ┆ 0.002861   ┆ 0.003031  │
│ 0.0325    ┆ 0.000023        ┆ 0.003941   ┆ 0.00523   │
│ …         ┆ …               ┆ …          ┆ …         │
│ 26.9725   ┆ 0.000444        ┆ 1.732643   ┆ -0.000004 │
│ 26.979167 ┆ 0.000296        ┆ 1.731815   ┆ -0.000128 │
│ 26.985833 ┆ 0.000094        ┆ 1.731004   ┆ -0.000105 │
│ 26.9925   ┆ 0.000108        ┆ 1.730043   ┆ 0.000064  │
│ 26.999167 ┆ -4.4409e-16     ┆ 1.728989   ┆ 0.000379  │
└───────────┴─────────────────┴────────────┴───────────┘

:NdOverlay   [Variable]
   :Curve   [time]   (value)

Good result with a window length of 5. Now input that into the function

In [17]:
def calc_deriv_subtraction_after_baseline_corr_and_smooth(df):
    out = df.rename({"smoothed": "signal"}).pipe(calculate_derivative_subtractions)

    display(out)
    display(
        out.plot(
            x="time",
            y=["signal", "signal_adjusted_2nd_diff", "double_subtraction"],
            alpha=[0.5, 0.5],
        ).opts(height=750, width=1000)
    )

    return out


smoothed_double_sub = smoothed_signal.pipe(
    calc_deriv_subtraction_after_baseline_corr_and_smooth
)

shape: (4_050, 11)
┌────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┐
│ time   ┆ adjust ┆ backgr ┆ signal ┆ first_ ┆ second ┆ weight ┆ signal ┆ weight ┆ signal ┆ double │
│ ---    ┆ ed_sig ┆ ound   ┆ ---    ┆ centra ┆ _centr ┆ ed_fir ┆ _adjus ┆ ed_sec ┆ _adjus ┆ _subtr │
│ f64    ┆ nal    ┆ ---    ┆ f64    ┆ l_diff ┆ al_dif ┆ st_dif ┆ ted_fi ┆ ond_di ┆ ted_2n ┆ action │
│        ┆ ---    ┆ f64    ┆        ┆ ---    ┆ f      ┆ f      ┆ rst_di ┆ ff     ┆ d_diff ┆ ---    │
│        ┆ f64    ┆        ┆        ┆ f64    ┆ ---    ┆ ---    ┆ ff     ┆ ---    ┆ ---    ┆ f64    │
│        ┆        ┆        ┆        ┆        ┆ f64    ┆ f64    ┆ ---    ┆ f64    ┆ f64    ┆        │
│        ┆        ┆        ┆        ┆        ┆        ┆        ┆ f64    ┆        ┆        ┆        │
╞════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╡
│ 0.0058 ┆ 2.2204 ┆ 0.0019 ┆ -0.005 ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   │
│ 33     ┆ e-16   ┆ 52     ┆ 903    ┆        ┆        ┆        ┆        ┆        ┆        ┆        │
│ 0.0125 ┆ -6.661 ┆ 0.0018 ┆ -0.002 ┆ 0.2379 ┆ -2.190 ┆ 0.0047 ┆ -0.007 ┆ -0.001 ┆ -0.001 ┆ -0.005 │
│        ┆ 3e-16  ┆ 25     ┆ 536    ┆ 54     ┆ 423    ┆ 59     ┆ 295    ┆ 314    ┆ 221    ┆ 98     │
│ 0.0191 ┆ -4.440 ┆ 0.0020 ┆ 0.0004 ┆ 0.2087 ┆ -2.190 ┆ 0.0041 ┆ -0.003 ┆ -0.001 ┆ 0.0017 ┆ -0.002 │
│ 67     ┆ 9e-16  ┆ 04     ┆ 42     ┆ 48     ┆ 423    ┆ 75     ┆ 733    ┆ 314    ┆ 57     ┆ 418    │
│ 0.0258 ┆ -4.440 ┆ 0.0028 ┆ 0.0030 ┆ 0.1795 ┆ -2.190 ┆ 0.0035 ┆ -0.000 ┆ -0.001 ┆ 0.0043 ┆ 0.0007 │
│ 33     ┆ 9e-16  ┆ 61     ┆ 31     ┆ 42     ┆ 423    ┆ 91     ┆ 56     ┆ 314    ┆ 45     ┆ 54     │
│ 0.0325 ┆ 0.0000 ┆ 0.0039 ┆ 0.0052 ┆ 0.1503 ┆ -2.190 ┆ 0.0030 ┆ 0.0022 ┆ -0.001 ┆ 0.0065 ┆ 0.0035 │
│        ┆ 23     ┆ 41     ┆ 3      ┆ 37     ┆ 423    ┆ 07     ┆ 23     ┆ 314    ┆ 44     ┆ 38     │
│ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      │
│ 26.972 ┆ 0.0004 ┆ 1.7326 ┆ -0.000 ┆ -0.014 ┆ 0.8227 ┆ -0.000 ┆ 0.0002 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 5      ┆ 44     ┆ 43     ┆ 004    ┆ 763    ┆ 69     ┆ 295    ┆ 91     ┆ 94     ┆ 498    ┆ 202    │
│ 26.979 ┆ 0.0002 ┆ 1.7318 ┆ -0.000 ┆ -0.003 ┆ 0.8227 ┆ -0.000 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 167    ┆ 96     ┆ 15     ┆ 128    ┆ 793    ┆ 69     ┆ 076    ┆ 052    ┆ 94     ┆ 621    ┆ 545    │
│ 26.985 ┆ 0.0000 ┆ 1.7310 ┆ -0.000 ┆ 0.0071 ┆ 0.8227 ┆ 0.0001 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 833    ┆ 94     ┆ 04     ┆ 105    ┆ 77     ┆ 69     ┆ 44     ┆ 249    ┆ 94     ┆ 599    ┆ 742    │
│ 26.992 ┆ 0.0001 ┆ 1.7300 ┆ 0.0000 ┆ 0.0181 ┆ 0.8227 ┆ 0.0003 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 5      ┆ 08     ┆ 43     ┆ 64     ┆ 48     ┆ 69     ┆ 63     ┆ 299    ┆ 94     ┆ 43     ┆ 793    │
│ 26.999 ┆ -4.440 ┆ 1.7289 ┆ 0.0003 ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   │
│ 167    ┆ 9e-16  ┆ 89     ┆ 79     ┆        ┆        ┆        ┆        ┆        ┆        ┆        │
└────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┘

shape: (4_050, 11)
┌────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┬────────┐
│ time   ┆ adjust ┆ backgr ┆ signal ┆ first_ ┆ second ┆ weight ┆ signal ┆ weight ┆ signal ┆ double │
│ ---    ┆ ed_sig ┆ ound   ┆ ---    ┆ centra ┆ _centr ┆ ed_fir ┆ _adjus ┆ ed_sec ┆ _adjus ┆ _subtr │
│ f64    ┆ nal    ┆ ---    ┆ f64    ┆ l_diff ┆ al_dif ┆ st_dif ┆ ted_fi ┆ ond_di ┆ ted_2n ┆ action │
│        ┆ ---    ┆ f64    ┆        ┆ ---    ┆ f      ┆ f      ┆ rst_di ┆ ff     ┆ d_diff ┆ ---    │
│        ┆ f64    ┆        ┆        ┆ f64    ┆ ---    ┆ ---    ┆ ff     ┆ ---    ┆ ---    ┆ f64    │
│        ┆        ┆        ┆        ┆        ┆ f64    ┆ f64    ┆ ---    ┆ f64    ┆ f64    ┆        │
│        ┆        ┆        ┆        ┆        ┆        ┆        ┆ f64    ┆        ┆        ┆        │
╞════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╪════════╡
│ 0.0058 ┆ 2.2204 ┆ 0.0019 ┆ -0.005 ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   │
│ 33     ┆ e-16   ┆ 52     ┆ 903    ┆        ┆        ┆        ┆        ┆        ┆        ┆        │
│ 0.0125 ┆ -6.661 ┆ 0.0018 ┆ -0.002 ┆ 0.2379 ┆ -2.190 ┆ 0.0047 ┆ -0.007 ┆ -0.001 ┆ -0.001 ┆ -0.005 │
│        ┆ 3e-16  ┆ 25     ┆ 536    ┆ 54     ┆ 423    ┆ 59     ┆ 295    ┆ 314    ┆ 221    ┆ 98     │
│ 0.0191 ┆ -4.440 ┆ 0.0020 ┆ 0.0004 ┆ 0.2087 ┆ -2.190 ┆ 0.0041 ┆ -0.003 ┆ -0.001 ┆ 0.0017 ┆ -0.002 │
│ 67     ┆ 9e-16  ┆ 04     ┆ 42     ┆ 48     ┆ 423    ┆ 75     ┆ 733    ┆ 314    ┆ 57     ┆ 418    │
│ 0.0258 ┆ -4.440 ┆ 0.0028 ┆ 0.0030 ┆ 0.1795 ┆ -2.190 ┆ 0.0035 ┆ -0.000 ┆ -0.001 ┆ 0.0043 ┆ 0.0007 │
│ 33     ┆ 9e-16  ┆ 61     ┆ 31     ┆ 42     ┆ 423    ┆ 91     ┆ 56     ┆ 314    ┆ 45     ┆ 54     │
│ 0.0325 ┆ 0.0000 ┆ 0.0039 ┆ 0.0052 ┆ 0.1503 ┆ -2.190 ┆ 0.0030 ┆ 0.0022 ┆ -0.001 ┆ 0.0065 ┆ 0.0035 │
│        ┆ 23     ┆ 41     ┆ 3      ┆ 37     ┆ 423    ┆ 07     ┆ 23     ┆ 314    ┆ 44     ┆ 38     │
│ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      ┆ …      │
│ 26.972 ┆ 0.0004 ┆ 1.7326 ┆ -0.000 ┆ -0.014 ┆ 0.8227 ┆ -0.000 ┆ 0.0002 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 5      ┆ 44     ┆ 43     ┆ 004    ┆ 763    ┆ 69     ┆ 295    ┆ 91     ┆ 94     ┆ 498    ┆ 202    │
│ 26.979 ┆ 0.0002 ┆ 1.7318 ┆ -0.000 ┆ -0.003 ┆ 0.8227 ┆ -0.000 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 167    ┆ 96     ┆ 15     ┆ 128    ┆ 793    ┆ 69     ┆ 076    ┆ 052    ┆ 94     ┆ 621    ┆ 545    │
│ 26.985 ┆ 0.0000 ┆ 1.7310 ┆ -0.000 ┆ 0.0071 ┆ 0.8227 ┆ 0.0001 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 833    ┆ 94     ┆ 04     ┆ 105    ┆ 77     ┆ 69     ┆ 44     ┆ 249    ┆ 94     ┆ 599    ┆ 742    │
│ 26.992 ┆ 0.0001 ┆ 1.7300 ┆ 0.0000 ┆ 0.0181 ┆ 0.8227 ┆ 0.0003 ┆ -0.000 ┆ 0.0004 ┆ -0.000 ┆ -0.000 │
│ 5      ┆ 08     ┆ 43     ┆ 64     ┆ 48     ┆ 69     ┆ 63     ┆ 299    ┆ 94     ┆ 43     ┆ 793    │
│ 26.999 ┆ -4.440 ┆ 1.7289 ┆ 0.0003 ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   ┆ null   │
│ 167    ┆ 9e-16  ┆ 89     ┆ 79     ┆        ┆        ┆        ┆        ┆        ┆        ┆        │
└────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┴────────┘

:NdOverlay   [Variable]
   :Curve   [time]   (value)

Didnt appear to make a difference, but I cant go higher than 5 (data not shown) without losing peak resolution. Interesting problem.

Now I am curious, what would the data look like if i set all values less than say 1E-6 to zero?

In [18]:
def filter_small_values(df: pl.DataFrame, threshold: float = 1e-1):
    df = df.with_columns(
        pl.when(pl.col("double_subtraction").le(threshold))
        .then(pl.lit(0))
        .otherwise(pl.col("double_subtraction"))
        .alias("infintesimal_filtered")
    )

    return df


filtered = smoothed_double_sub.pipe(filter_small_values)
display(filtered)
display(
    filtered.plot(
        x="time",
        y=["double_subtraction", "infintesimal_filtered"],
        alpha=[0.75, 0.75],
        height=500,
        width=1000,
        grid=True,
    )
)

shape: (4_050, 12)
┌────────┬────────┬────────┬───────┬───────┬───────┬───────┬───────┬───────┬───────┬───────┬───────┐
│ time   ┆ adjust ┆ backgr ┆ signa ┆ first ┆ secon ┆ weigh ┆ signa ┆ weigh ┆ signa ┆ doubl ┆ infin │
│ ---    ┆ ed_sig ┆ ound   ┆ l     ┆ _cent ┆ d_cen ┆ ted_f ┆ l_adj ┆ ted_s ┆ l_adj ┆ e_sub ┆ tesim │
│ f64    ┆ nal    ┆ ---    ┆ ---   ┆ ral_d ┆ tral_ ┆ irst_ ┆ usted ┆ econd ┆ usted ┆ tract ┆ al_fi │
│        ┆ ---    ┆ f64    ┆ f64   ┆ iff   ┆ diff  ┆ diff  ┆ _firs ┆ _diff ┆ _2nd_ ┆ ion   ┆ ltere │
│        ┆ f64    ┆        ┆       ┆ ---   ┆ ---   ┆ ---   ┆ t_dif ┆ ---   ┆ diff  ┆ ---   ┆ d     │
│        ┆        ┆        ┆       ┆ f64   ┆ f64   ┆ f64   ┆ f     ┆ f64   ┆ ---   ┆ f64   ┆ ---   │
│        ┆        ┆        ┆       ┆       ┆       ┆       ┆ ---   ┆       ┆ f64   ┆       ┆ f64   │
│        ┆        ┆        ┆       ┆       ┆       ┆       ┆ f64   ┆       ┆       ┆       ┆       │
╞════════╪════════╪════════╪═══════╪═══════╪═══════╪═══════╪═══════╪═══════╪═══════╪═══════╪═══════╡
│ 0.0058 ┆ 2.2204 ┆ 0.0019 ┆ -0.00 ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  │
│ 33     ┆ e-16   ┆ 52     ┆ 5903  ┆       ┆       ┆       ┆       ┆       ┆       ┆       ┆       │
│ 0.0125 ┆ -6.661 ┆ 0.0018 ┆ -0.00 ┆ 0.237 ┆ -2.19 ┆ 0.004 ┆ -0.00 ┆ -0.00 ┆ -0.00 ┆ -0.00 ┆ 0.0   │
│        ┆ 3e-16  ┆ 25     ┆ 2536  ┆ 954   ┆ 0423  ┆ 759   ┆ 7295  ┆ 1314  ┆ 1221  ┆ 598   ┆       │
│ 0.0191 ┆ -4.440 ┆ 0.0020 ┆ 0.000 ┆ 0.208 ┆ -2.19 ┆ 0.004 ┆ -0.00 ┆ -0.00 ┆ 0.001 ┆ -0.00 ┆ 0.0   │
│ 67     ┆ 9e-16  ┆ 04     ┆ 442   ┆ 748   ┆ 0423  ┆ 175   ┆ 3733  ┆ 1314  ┆ 757   ┆ 2418  ┆       │
│ 0.0258 ┆ -4.440 ┆ 0.0028 ┆ 0.003 ┆ 0.179 ┆ -2.19 ┆ 0.003 ┆ -0.00 ┆ -0.00 ┆ 0.004 ┆ 0.000 ┆ 0.0   │
│ 33     ┆ 9e-16  ┆ 61     ┆ 031   ┆ 542   ┆ 0423  ┆ 591   ┆ 056   ┆ 1314  ┆ 345   ┆ 754   ┆       │
│ 0.0325 ┆ 0.0000 ┆ 0.0039 ┆ 0.005 ┆ 0.150 ┆ -2.19 ┆ 0.003 ┆ 0.002 ┆ -0.00 ┆ 0.006 ┆ 0.003 ┆ 0.0   │
│        ┆ 23     ┆ 41     ┆ 23    ┆ 337   ┆ 0423  ┆ 007   ┆ 223   ┆ 1314  ┆ 544   ┆ 538   ┆       │
│ …      ┆ …      ┆ …      ┆ …     ┆ …     ┆ …     ┆ …     ┆ …     ┆ …     ┆ …     ┆ …     ┆ …     │
│ 26.972 ┆ 0.0004 ┆ 1.7326 ┆ -0.00 ┆ -0.01 ┆ 0.822 ┆ -0.00 ┆ 0.000 ┆ 0.000 ┆ -0.00 ┆ -0.00 ┆ 0.0   │
│ 5      ┆ 44     ┆ 43     ┆ 0004  ┆ 4763  ┆ 769   ┆ 0295  ┆ 291   ┆ 494   ┆ 0498  ┆ 0202  ┆       │
│ 26.979 ┆ 0.0002 ┆ 1.7318 ┆ -0.00 ┆ -0.00 ┆ 0.822 ┆ -0.00 ┆ -0.00 ┆ 0.000 ┆ -0.00 ┆ -0.00 ┆ 0.0   │
│ 167    ┆ 96     ┆ 15     ┆ 0128  ┆ 3793  ┆ 769   ┆ 0076  ┆ 0052  ┆ 494   ┆ 0621  ┆ 0545  ┆       │
│ 26.985 ┆ 0.0000 ┆ 1.7310 ┆ -0.00 ┆ 0.007 ┆ 0.822 ┆ 0.000 ┆ -0.00 ┆ 0.000 ┆ -0.00 ┆ -0.00 ┆ 0.0   │
│ 833    ┆ 94     ┆ 04     ┆ 0105  ┆ 177   ┆ 769   ┆ 144   ┆ 0249  ┆ 494   ┆ 0599  ┆ 0742  ┆       │
│ 26.992 ┆ 0.0001 ┆ 1.7300 ┆ 0.000 ┆ 0.018 ┆ 0.822 ┆ 0.000 ┆ -0.00 ┆ 0.000 ┆ -0.00 ┆ -0.00 ┆ 0.0   │
│ 5      ┆ 08     ┆ 43     ┆ 064   ┆ 148   ┆ 769   ┆ 363   ┆ 0299  ┆ 494   ┆ 043   ┆ 0793  ┆       │
│ 26.999 ┆ -4.440 ┆ 1.7289 ┆ 0.000 ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  ┆ null  │
│ 167    ┆ 9e-16  ┆ 89     ┆ 379   ┆       ┆       ┆       ┆       ┆       ┆       ┆       ┆       │
└────────┴────────┴────────┴───────┴───────┴───────┴───────┴───────┴───────┴───────┴───────┴───────┘

:NdOverlay   [Variable]
   :Curve   [time]   (value)

Now, while the peaks are not fully resolved, and the 4 - 5 min region is looking very troubling, there seems to be some hope of reasonable window sizes. I am expecting at least 10 individual peak windows. Will this be the case? if not, I need to reassess the 'windowing' algorithm.

Side note - the new algorithm would simply demarcate via the baseline - if the baseline is zero after the infintesimal filter, its interpeak. if not, its peak.

Side note side note - DAG pipelines are what you need for problems such as this, where you need to apply stages in different  orders, possibly repeated. (I think?)

Addendum: I am not happy with the baseline subtraction from SNIP. Since N_ITER is the only variable, its not flexible enough, and not able to adapt to the different regions of the signal, i.e. 0.8 to 1.56. BEADS (see: https://www.sciencedirect.com/science/article/abs/pii/S0169743914002032?via%3Dihub) is a newer method with a python implementation (see: https://github.com/skotaro/pybeads). Lets test it out [here](preprocessing_2_beads.ipynb). Results - BEAD package is not documented enough for use, the default settings and my tinkering have produced an underfit estimation that obliterates too much peak information.

In [19]:
def window_after_infintesimal(df: pl.DataFrame):
    """
    To skip 'signal_adjustment' I need to set "signal_adjusted" to True and set 'signal' to an input, and rename the columns in df. Might as well skip 'injest_signal' while we're at it.
    """
    # display(df)
    input_signal = df.with_row_index("idx").select(
        pl.col("idx").cast(int),
        pl.col("time"),
        pl.col("signal"),
        pl.col("infintesimal_filtered").alias("adjusted_signal").fill_null(0),
        pl.col("background"),
    )

    prepro = PreProcesser()
    prepro.signal_injested = True
    prepro.signal_adjusted = True

    prepro.signal = prepro.signal.join(
        input_signal,
        how="outer_coalesce",
        on=["idx", "time", "signal", "adjusted_signal", "background"],
    )

    prepro.map_peaks(find_peaks_kwargs={"prominence": 0.0001})
    prepro.map_windows()
    display(prepro.viz_preprocessing().opts(height=500, width=1250))
    # display(prepro.window_mapper.window_bounds_)

    display(prepro.signal)

    display(prepro.peak_map.maxima)


window_after_infintesimal(df=filtered)

# TODO: window the peak map in preprocessor. Investigate the number of peaks per window

/Users/jonathan/hplc-py/hplc_py/map_peaks/viz.py:144: UserWarning: whh plot not implemented
  warnings.warn("whh plot not implemented")


:Overlay
   .Curve.X              :Curve   [idx]   (X)
   .NdOverlay.Maxima     :NdOverlay   [p_idx]
      :Scatter   [idx]   (X)
   .NdOverlay.Base_edges :NdOverlay   [p_idx,msnt]
      :Curve   [idx]   (X)
   .NdOverlay.I          :NdOverlay   [Variable]
      :Curve   [idx]   (value)
   .VSpans.Interpeak_wdw :VSpans   [x0,x1]
   .Labels.I             :Labels   [x,y]   (w_idx)

shape: (4_050, 7)
┌──────┬───────────┬───────────┬─────────────────┬────────────┬───────────┬───────┐
│ idx  ┆ time      ┆ signal    ┆ adjusted_signal ┆ background ┆ w_type    ┆ w_idx │
│ ---  ┆ ---       ┆ ---       ┆ ---             ┆ ---        ┆ ---       ┆ ---   │
│ i64  ┆ f64       ┆ f64       ┆ f64             ┆ f64        ┆ str       ┆ i64   │
╞══════╪═══════════╪═══════════╪═════════════════╪════════════╪═══════════╪═══════╡
│ 0    ┆ 0.005833  ┆ -0.005903 ┆ 0.0             ┆ 0.001952   ┆ interpeak ┆ 0     │
│ 1    ┆ 0.0125    ┆ -0.002536 ┆ 0.0             ┆ 0.001825   ┆ interpeak ┆ 0     │
│ 2    ┆ 0.019167  ┆ 0.000442  ┆ 0.0             ┆ 0.002004   ┆ interpeak ┆ 0     │
│ 3    ┆ 0.025833  ┆ 0.003031  ┆ 0.0             ┆ 0.002861   ┆ interpeak ┆ 0     │
│ 4    ┆ 0.0325    ┆ 0.00523   ┆ 0.0             ┆ 0.003941   ┆ interpeak ┆ 0     │
│ …    ┆ …         ┆ …         ┆ …               ┆ …          ┆ …         ┆ …     │
│ 4045 ┆ 26.9725   ┆ -0.000004 ┆ 0.0             ┆ 1.732643   ┆ interpeak ┆ 26    │
│ 4046 ┆ 26.979167 ┆ -0.000128 ┆ 0.0             ┆ 1.731815   ┆ interpeak ┆ 26    │
│ 4047 ┆ 26.985833 ┆ -0.000105 ┆ 0.0             ┆ 1.731004   ┆ interpeak ┆ 26    │
│ 4048 ┆ 26.9925   ┆ 0.000064  ┆ 0.0             ┆ 1.730043   ┆ interpeak ┆ 26    │
│ 4049 ┆ 26.999167 ┆ 0.000379  ┆ 0.0             ┆ 1.728989   ┆ interpeak ┆ 26    │
└──────┴───────────┴───────────┴─────────────────┴────────────┴───────────┴───────┘

p_idx     loc  dim       value
0        0  maxima  idx  106.000000
1        1  maxima  idx  132.000000
2        2  maxima  idx  148.000000
3        3  maxima  idx  166.000000
4        4  maxima  idx  189.000000
..     ...     ...  ...         ...
165     80  maxima    X    0.371374
166     81  maxima    X    0.695790
167     82  maxima    X    0.129392
168     83  maxima    X    0.138736
169     84  maxima    X    0.181934

[170 rows x 4 columns]

Great success! Applicatino of the above has resulted in 25 individual peak windows 